# Copying Adam Taylor's PCam5c driver to python top layer

In [ ]:
from pynq import Overlay
from kv260 import BaseOverlay
from pynq.lib.iic import AxiIIC 
from pynq.lib.video import *
import numpy as np
from time import sleep
import PIL.Image

import periphery 
from periphery import MMIO

adams = Overlay("modified_taylor_bits/taylor_v1.bit", ignore_version=True)
#base = BaseOverlay("base.bit")

In [ ]:
'''Instantiating a branchof the Default IP Class (overlay.py file) for each ip '''

vdma = adams.axi_vdma_0
demosaic = adams.v_demosaic_0
gamma = adams.v_gamma_lut_0

In [ ]:
'''Extracting base address and size/length of memory region from the Default_IP class '''
gamma_base_addr = gamma.mmio.base_addr
gamma_size = gamma.mmio.length

'''Intanstiating the new periphery.mmio class by feeding it the base address and size of memory allocation for gamma IP, as extracted from previous class '''
periphery = MMIO(gamma_base_addr, gamma_size)

print(periphery.size)

def gamma_calc(gamma_val):
    gamma_reg = []
    i = 0
    for i in range(0,256):
        gamma_reg.append( 256*(i/256)**(1/gamma_val) )
    return gamma_reg

def count_loop(offset, gamma_corr):
    count= 0 
    while count < 0x200:
        periphery.write16(offset + count, int(count/2))
        print(count)
        count = count + 2

In [ ]:
def demosaic_config(width, height):
    demosaic.write(0x10, width)
    demosaic.write(0x18, height)
    demosaic.write(0x28, 0x03)
    
    d_read = demosaic.read(0x00)
    print(hex(d_read))
    
    demosaic.write(0x00,0x81)
    
    d_read = demosaic.read(0x00)
    print(hex(d_read))
    return 

In [ ]:
def gamma_config(width, height):
    gamma.write(0x10, width)
    gamma.write(0x18, height)
    gamma.write(0x20, 0x00)
    
    gamma_reg = gamma_calc(1.2)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x800 + i, int(gamma_reg[int(i/2)]))
        
    gamma_reg = gamma_calc(1.2)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x1000 + i, int(gamma_reg[int(i/2)])) 
        
    gamma_reg = gamma_calc(1.1)
    #print(gamma_reg,'\n')
    
    for i in range(0,512,2): 
        periphery.write16( 0x1800 + i, int(gamma_reg[int(i/2)]))

    gamma.write(0x00, 0x81)
    #gamma.read(0x00)
    return 

In [ ]:
iic = adams.axi_iic_0

iic_cam_addr = 0x3c
sw_iic_addr = 0x74
rx_data = bytes(10)
tx_data = [0,0,0,0,0,0]

In [ ]:
def setup_i2c_switch():
    tx_data[0] = 0x04
    iic.send(sw_iic_addr, tx_data, 1)               

In [ ]:
def detect_camera():
    tx_data[0] = 0x31;  tx_data[1] = 0x00;

    iic.send(iic_cam_addr, tx_data, 2)        
    print('send complete')
    sleep(0.5)
    
    status = iic.receive(iic_cam_addr, rx_data, 1)
    if hex(rx_data[0]) != '0x78':
        print("camera not detected")
        print(rx_data)        
    else:
        print("camera detected")            

In [ ]:
def reset_camera(cfg):   
    tx_data[0] = 0x30; tx_data[1] = 0x08; tx_data[2] = cfg;
    
    iic.send(iic_cam_addr, tx_data, 3)          

In [ ]:
def camera_chip_id_low():   
    tx_data[0] = 0x30;  tx_data[1] = 0x0A;

    iic.send(iic_cam_addr, tx_data, 2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x56':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [ ]:
def camera_chip_id_high():    
    tx_data[0] = 0x30;  tx_data[1] = 0x0B;

    iic.send(iic_cam_addr,tx_data,2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x40':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [ ]:
def camera_system_clk(): 
    tx_data[0] = 0x31;  tx_data[1] = 0x03;
    tx_data[2] = 0x11

    iic.send(iic_cam_addr, tx_data, 3) 

In [ ]:
def iic_tx(reg, val):
    tx_data[0] = (reg>>8) & (0xFF);
    tx_data[1] = reg & (0xFF);
    tx_data[2] = val
    
    iic.send(iic_cam_addr, tx_data, 3) 
    print("sent -> {} {} {}".format(hex(tx_data[0]),hex(tx_data[1]),hex(tx_data[2])))

In [ ]:
def vdma_init(videomode):
    if vdma.readchannel.running: 
        vdma.readchannel.stop()

    vdma.readchannel.mode = videomode

Start Driver Steps

In [ ]:
setup_i2c_switch()

In [ ]:
detect_camera()

In [ ]:
videomode = VideoMode(1280,720,24)
                      
vdma_init(videomode)  

In [ ]:
demosaic_config(1280, 720)
gamma_config(1280, 720)

In [ ]:
%run pcam_cfg.ipynb
#camera_system_clk()
iic_tx(0x3008, 0x82)
sleep(1.0)

iic_tx(0x3008, 0x42)
setting_func(cfg_init)
#iic_tx(0x3008, 0x02)

#iic_tx(0x3008, 0x42)
setting_func(cfg_720p_60fps)
#iic_tx(0x3008, 0x02)

#iic_tx(0x3008, 0x42)
setting_func(cfg_simple_awb)
iic_tx(0x3008, 0x02)

vdma.readchannel.start()

In [ ]:
vdma.readchannel.start()
frame = vdma.readchannel.readframe()
PIL.Image.fromarray(frame[:,:,[2,1,0]])

In [ ]:
import time
num_frames = 20000000
start = time.time()

displayport = DisplayPort()

displayport.configure(videomode, PIXEL_RGB)

for _ in range (num_frames):
    frame = displayport.newframe()
    frame[:] = vdma.readchannel.readframe()
    displayport.writeframe(frame)

end = time.time()
duration = end - start
print(f"Took {duration} seconds at {num_frames / duration} FPS")

In [ ]:
displayport.close()

vdma.readchannel.stop()

#base.free()

In [ ]:
displayport.modes